In [1]:
!git clone https://www.github.com/nvidia/apex
!cd ..
!pip install -v --no-cache-dir ./apex
!pip install simpletransformers

Cloning into 'apex'...
remote: Enumerating objects: 9513, done.
remote: Counting objects: 100% (584/584), done.
remote: Compressing objects: 100% (392/392), done.
remote: Total 9513 (delta 326), reused 358 (delta 176), pack-reused 8929
Receiving objects: 100% (9513/9513), 14.80 MiB | 20.60 MiB/s, done.
Resolving deltas: 100% (6439/6439), done.
Using pip 21.1.3 from /usr/local/lib/python3.7/dist-packages/pip (python 3.7)
Value for scheme.platlib does not match. Please report this to <https://github.com/pypa/pip/issues/9617>
distutils: /usr/local/lib/python3.7/dist-packages
sysconfig: /usr/lib/python3.7/site-packages
Value for scheme.purelib does not match. Please report this to <https://github.com/pypa/pip/issues/9617>
distutils: /usr/local/lib/python3.7/dist-packages
sysconfig: /usr/lib/python3.7/site-packages
Value for scheme.headers does not match. Please report this to <https://github.com/pypa/pip/issues/9617>
distutils: /usr/local/include/python3.7/UNKNOWN
sysconfig: /usr/include/p

In [1]:
import pandas as pd
import numpy as np
import time
from sklearn.model_selection import StratifiedShuffleSplit, GroupShuffleSplit
from simpletransformers.ner import NERModel
from seqeval.metrics import f1_score, classification_report

In [2]:
shuffle_split = GroupShuffleSplit(n_splits=5, test_size=0.3, random_state=2021)

In [3]:
df = pd.read_csv("disengagement_aggregated.csv")
df.words = df.words.astype('str')
df_post_train = pd.read_csv("post_train.csv")
df_post_test = pd.read_csv("post_test.csv")
df_post_train.words = df_post_train.words.astype(str)
df_post_train.labels = df_post_train.labels.astype(str)
df_post_test.words = df_post_test.words.astype(str)
df_post_test.labels = df_post_test.labels.astype(str)

## Post train BERT

In [ ]:
start = time.time()
tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
model_args = {
    "output_dir": f"post_output/",
    'best_model_dir': f"post_output/best_model/",
    "manual_seed": 2020,
    "do_lower_case": True,
    "num_train_epochs": 8,
    "learning_rate": 5e-5,
    "max_seq_length": 128,

    "evaluate_during_training": True, 
    "evaluate_during_training_verbose": True,
    "evaluate_during_training_steps": 4450,
    "save_eval_checkpoints": False,

    "use_early_stopping": False,
    "early_stopping_delta": 0.001,
    "early_stopping_metric": "f1_score",
    "early_stopping_metric_minimize": False,
    "early_stopping_patience": 3,

    'overwrite_output_dir': True,
}
labels = df_post_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
#model = NERModel('electra', 'google/electra-base-discriminator', labels=tags, use_cuda = True, args=model_args)
model = NERModel('bert', 'bert-base-cased', labels=tags, use_cuda = True, args=model_args)
#model = NERModel('xlnet', 'xlnet-base-cased', labels=tags, use_cuda = True, args=model_args)
#model = NERModel('roberta', 'roberta-base', labels=tags, use_cuda = True, args=model_args)

model.train_model(df_post_train, eval_data = df_post_test)
result, model_outputs, predictions = model.eval_model(df_post_test)
end = time.time()
print(end - start)


Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/416M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForTokenClassification: ['cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cas

Downloading:   0%|          | 0.00/208k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

...

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/99 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/99 [00:00<?, ?it/s]

754.4118614196777


In [ ]:
for _, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
    "output_dir": f"post_output/",
    'best_model_dir': f"post_output/best_model/",
    "manual_seed": 2020,
    "do_lower_case": True,
    "num_train_epochs": 8,
    "learning_rate": 5e-5,
    "max_seq_length": 128,

    "evaluate_during_training": True, 
    "evaluate_during_training_verbose": True,
    "evaluate_during_training_steps": 4450,
    "save_eval_checkpoints": False,

    "use_early_stopping": False,
    "early_stopping_delta": 0.001,
    "early_stopping_metric": "f1_score",
    "early_stopping_metric_minimize": False,
    "early_stopping_patience": 3,

    'overwrite_output_dir': True,
}
  labels = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  #model = NERModel('electra', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  model = NERModel('bert', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  #model = NERModel('xlnet', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  #model = NERModel('roberta', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)

  result, model_outputs, predictions = model.eval_model(df_test)
  ind = []
  for i in range(len(labels)):
    if len(labels[i]) == len(predictions[i]):
      ind.append(i)
  labels = np.array(labels)[ind]
  predictions = np.array(predictions)[ind]
  print(classification_report(labels, predictions))

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:37: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:38: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


              precision    recall  f1-score   support

           C       0.74      0.60      0.66       124
          CE       0.75      0.30      0.43        10
           E       0.57      0.54      0.56       100

   micro avg       0.66      0.56      0.61       234
   macro avg       0.69      0.48      0.55       234
weighted avg       0.67      0.56      0.61       234



  0%|          | 0/1 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.66      0.62      0.64       111
          CE       1.00      0.33      0.50         3
           E       0.53      0.54      0.53        93

   micro avg       0.60      0.58      0.59       207
   macro avg       0.73      0.50      0.56       207
weighted avg       0.61      0.58      0.59       207



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.64      0.61      0.62       120
          CE       0.67      0.25      0.36         8
           E       0.50      0.51      0.51       101

   micro avg       0.58      0.55      0.57       229
   macro avg       0.60      0.46      0.50       229
weighted avg       0.58      0.55      0.56       229



In [ ]:
weighted_f1 = (0.61+0.61+0.55+0.59+0.56) / 5
print(f"weighted_f1 for bert + post train is {weighted_f1}")
weighted_f1_std = np.std([0.61, 0.61, 0.55, 0.59, 0.56])
print(f"weighted_f1 for bert + post train is {weighted_f1_std}")

weighted_f1 for bert + post train is 0.584
weighted_f1 for bert + post train is 0.024979991993593565


## Save best post train model for later use

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!cp -r /content/post_output/best_model/ /content/drive/MyDrive/cause_and_effect/best_model/

cp: cannot create directory '/content/drive/MyDrive/cause_and_effect/best_model/': No such file or directory


## Bert + post train + fine tuning

In [ ]:
start = time.time()
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"electra_all_outputs_{i}/",
      'best_model_dir': f"electra_all_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 8,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  #model_ = NERModel('electra', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  model_ = NERModel('bert', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  #model_ = NERModel('xlnet', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)
  #model_ = NERModel('roberta', '/content/post_output/best_model/', labels=tags, use_cuda = True, args=model_args)

  model_.train_model(df_train, eval_data = df_test)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  ind = []
  for i in range(len(labels_)):
    if len(labels_[i]) == len(predictions_[i]):
      ind.append(i)
  labels_ = np.array(labels_)[ind]
  predictions_ = np.array(predictions_)[ind]
  print(classification_report(labels_, predictions_))
  i += 1
end = time.time()
print(end - start)

  0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:309: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


Epoch:   0%|          | 0/8 [00:00<?, ?it/s]

Running Epoch 0 of 8:   0%|          | 0/92 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.84      0.89      0.86       120
          CE       0.60      0.75      0.67         8
           E       0.78      0.91      0.84       101

   micro avg       0.80      0.90      0.85       229
   macro avg       0.74      0.85      0.79       229
weighted avg       0.80      0.90      0.85       229

664.8805510997772


In [ ]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"electra_all_outputs_{i}/",
      'best_model_dir': f"electra_all_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 8,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  #model_ = NERModel('electra', f"electra_all_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  model_ = NERModel('bert', f"electra_all_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  #model_ = NERModel('xlnet', f"electra_all_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  #model_ = NERModel('roberta', f"electra_all_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)

  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  ind = []
  for i in range(len(labels_)):
    if len(labels_[i]) == len(predictions_[i]):
      ind.append(i)
  labels_ = np.array(labels_)[ind]
  predictions_ = np.array(predictions_)[ind]
  print(classification_report(labels_, predictions_, 2))
  i += 1

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:42: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:43: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


              precision    recall  f1-score   support

           C       0.87      0.88      0.88       124
          CE       0.88      0.70      0.78        10
           E       0.92      0.89      0.90       100

   micro avg       0.89      0.88      0.88       234
   macro avg       0.89      0.82      0.85       234
weighted avg       0.89      0.88      0.88       234



  0%|          | 0/1 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.93      0.95      0.94       111
          CE       1.00      1.00      1.00         3
           E       0.83      0.91      0.87        93

   micro avg       0.89      0.93      0.91       207
   macro avg       0.92      0.95      0.94       207
weighted avg       0.89      0.93      0.91       207



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.83      0.92      0.87       120
          CE       1.00      0.88      0.93         8
           E       0.83      0.90      0.87       101

   micro avg       0.84      0.91      0.87       229
   macro avg       0.89      0.90      0.89       229
weighted avg       0.84      0.91      0.87       229



In [ ]:
weighted_f1 = (0.88 + 0.95 + 0.90 + 0.91 + 0.87) / 5
print(f"weighted_f1 for bert + post train + fine tuning is {weighted_f1}")
weighted_f1_std = np.std([0.88, 0.95, 0.90, 0.91, 0.87])
print(f"weighted_f1 for bert + post train + fine tuning is {weighted_f1_std}")

weighted_f1 for bert + post train + fine tuning is 0.9019999999999999
weighted_f1 for bert + post train is 0.027856776554368225


## Bert + fine tunig

In [ ]:
weighted_f1 = (0.98 + 0.96 + 0.94 + 0.92 + 0.86) / 5
print(f"weighted_f1 for bert +  fine tuning is {weighted_f1}")
weighted_f1_std = np.std([0.91, 0.92, 0.93, 0.92, 0.89])
print(f"weighted_f1 for bert +  fine tuning is {weighted_f1_std}")

weighted_f1 for bert +  fine tuning is 0.932
weighted_f1 for bert +  fine tuning is 0.013564659966250548


## BERT

In [4]:
start = time.time()
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"bert_outputs_{i}/",
      'best_model_dir': f"bert_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 8,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('bert', 'bert-base-cased', labels=tags, use_cuda = True, args=model_args)
  model_.train_model(df_train, eval_data = df_test)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_))
  i += 1
end = time.time()
print(end - start)

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/416M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForTokenClassification: ['cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cas

Downloading:   0%|          | 0.00/208k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.84      0.91      0.88       120
          CE       0.67      0.50      0.57         8
           E       0.81      0.86      0.83       101

   micro avg       0.82      0.87      0.85       229
   macro avg       0.77      0.76      0.76       229
weighted avg       0.82      0.87      0.85       229

687.2931671142578


In [5]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"bert_outputs_{i}/",
      'best_model_dir': f"bert_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 10,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('bert', f"bert_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_, 2))
  i += 1

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.83      0.89      0.86       124
          CE       1.00      0.60      0.75        10
           E       0.92      0.90      0.91       100

   micro avg       0.87      0.88      0.87       234
   macro avg       0.92      0.80      0.84       234
weighted avg       0.87      0.88      0.87       234



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.86      0.89      0.88       111
          CE       1.00      0.67      0.80         3
           E       0.85      0.83      0.84        93

   micro avg       0.86      0.86      0.86       207
   macro avg       0.90      0.80      0.84       207
weighted avg       0.86      0.86      0.86       207



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.86      0.89      0.87       120
          CE       0.80      0.50      0.62         8
           E       0.85      0.87      0.86       101

   micro avg       0.85      0.87      0.86       229
   macro avg       0.83      0.75      0.78       229
weighted avg       0.85      0.87      0.86       229



In [ ]:
weighted_f1 = (0.87 + 0.87 + 0.86 + 0.86 + 0.86) / 5
print(f"weighted_f1 for bert +  fine tuning is {weighted_f1}")
weighted_f1_std = np.std([0.87, 0.87, 0.86, 0.86, 0.86])
print(f"weighted_f1 for bert +  fine tuning is {weighted_f1_std}")

weighted_f1 for bert +  fine tuning is 0.8640000000000001
weighted_f1 for bert +  fine tuning is 0.004898979485566361


## DistilBERT

In [ ]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"distillbert_outputs_{i}/",
      'best_model_dir': f"distillbert_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 10,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('distilbert', 'distilbert-base-cased', labels=tags, use_cuda = True, args=model_args)
  model_.train_model(df_train, eval_data = df_test)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_))
  i += 1

Downloading:   0%|          | 0.00/411 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/251M [00:00<?, ?B/s]

Some weights of the model checkpoint at distilbert-base-cased were not used when initializing DistilBertForTokenClassification: ['vocab_transform.weight', 'vocab_layer_norm.weight', 'vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias']
- This IS expected if you are initializing DistilBertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForTokenClassification were not initialized from the model checkpoint at distilbert-base-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this 

Downloading:   0%|          | 0.00/208k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.85      0.85      0.85       120
          CE       1.00      0.50      0.67         8
           E       0.77      0.81      0.79       101

   micro avg       0.82      0.82      0.82       229
   macro avg       0.87      0.72      0.77       229
weighted avg       0.82      0.82      0.82       229



In [ ]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"distillbert_outputs_{i}/",
      'best_model_dir': f"distillbert_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 10,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('distilbert', f"distillbert_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_, 2))
  i += 1

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.88      0.90      0.89       124
          CE       0.83      0.50      0.62        10
           E       0.89      0.89      0.89       100

   micro avg       0.88      0.88      0.88       234
   macro avg       0.87      0.76      0.80       234
weighted avg       0.88      0.88      0.88       234



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.84      0.92      0.88       111
          CE       1.00      0.67      0.80         3
           E       0.81      0.86      0.83        93

   micro avg       0.83      0.89      0.86       207
   macro avg       0.88      0.82      0.84       207
weighted avg       0.83      0.89      0.86       207



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.86      0.85      0.85       120
          CE       1.00      0.50      0.67         8
           E       0.89      0.85      0.87       101

   micro avg       0.87      0.84      0.86       229
   macro avg       0.91      0.73      0.80       229
weighted avg       0.88      0.84      0.85       229



In [ ]:
weighted_f1 = (0.88 + 0.85 + 0.89 + 0.86 + 0.85) / 5
print(f"weighted_f1 for distilbert + fine tuning is {weighted_f1}")

weighted_f1 for distilbert + fine tuning is 0.866


## Xlnet

In [ ]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"xlnet_outputs_{i}/",
      'best_model_dir': f"xlnet_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 10,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('xlnet', 'xlnet-base-cased', labels=tags, use_cuda = True, args=model_args)
  model_.train_model(df_train, eval_data = df_test)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_))
  i += 1

Downloading:   0%|          | 0.00/760 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/445M [00:00<?, ?B/s]

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForTokenClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForTokenClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Downloading:   0%|          | 0.00/779k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.32M [00:00<?, ?B/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.88      0.89      0.89       120
          CE       0.83      0.62      0.71         8
           E       0.76      0.87      0.81       101

   micro avg       0.82      0.87      0.85       229
   macro avg       0.83      0.80      0.80       229
weighted avg       0.83      0.87      0.85       229



In [ ]:
i = 0
for train_index, test_index in shuffle_split.split(df.words, df.labels, groups=df.sentence_id):
  df_train = df.loc[train_index,:]
  df_test = df.loc[test_index,:]
  tags = ['O', 'B-C', 'I-C', 'B-E', 'I-E', 'B-CE', 'I-CE']
  model_args = {
      "output_dir": f"xlnet_outputs_{i}/",
      'best_model_dir': f"xlnet_outputs_{i}/best_model/",
      "do_lower_case": False,
      "manual_seed": 2020,
      "num_train_epochs": 10,
      "learning_rate": 5e-5,
      "max_seq_length": 128,

      "evaluate_during_training": True, 
      "evaluate_during_training_verbose": True,
      "evaluate_during_training_steps": 4450,
      "save_eval_checkpoints": False,

      "use_early_stopping": True,
      "early_stopping_delta": 0.01,
      "early_stopping_metric": "f1_score",
      "early_stopping_metric_minimize": False,
      "early_stopping_patience": 3,

      'overwrite_output_dir': True,
      'save_optimizer_and_scheduler': False,
      'save_model_every_epoch': False,
      'save_steps': -1,
  }
  labels_ = df_test.groupby(['sentence_id'])['labels'].apply(list).to_list()
  model_ = NERModel('xlnet', f"xlnet_outputs_{i}/best_model/", labels=tags, use_cuda = True, args=model_args)
  result_, model_outputs_, predictions_ = model_.eval_model(df_test)
  print(classification_report(labels_, predictions_, 2))
  i += 1

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.84      0.90      0.87       124
          CE       1.00      0.80      0.89        10
           E       0.85      0.88      0.87       100

   micro avg       0.85      0.89      0.87       234
   macro avg       0.90      0.86      0.88       234
weighted avg       0.85      0.89      0.87       234



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.86      0.88      0.87       111
          CE       0.67      0.67      0.67         3
           E       0.82      0.82      0.82        93

   micro avg       0.84      0.85      0.84       207
   macro avg       0.78      0.79      0.78       207
weighted avg       0.84      0.85      0.84       207



  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           C       0.88      0.89      0.88       120
          CE       0.83      0.62      0.71         8
           E       0.81      0.86      0.84       101

   micro avg       0.85      0.87      0.86       229
   macro avg       0.84      0.79      0.81       229
weighted avg       0.85      0.87      0.86       229



In [ ]:
weighted_f1 = (0.87 + 0.87 + 0.90 + 0.84 + 0.86) / 5
print(f"weighted_f1 for distilbert + fine tuning is {weighted_f1}")

weighted_f1 for distilbert + fine tuning is 0.868
